# Task5

Index_X = FSR_for_force

Index_y = force

Data = Splited by Subject

## Run result

https://wandb.ai/seokjin/FSR-prediction/groups/FSR_Trainable_2023-07-05_22-10-54/workspace?workspace=user-seokjin

## Experiment id

FSR_Trainable_2023-07-05_22-10-54

In [1]:
def define_searchspace(trial):
    model = trial.suggest_categorical('model', ['fsr_model.LSTM', 'fsr_model.CNN_LSTM', 'fsr_model.ANN'])
    if model == 'fsr_model.LSTM':
        trial.suggest_categorical('model_args/hidden_size', [8, 16, 32, 64, 128])
        trial.suggest_int('model_args/num_layer', 1, 8)
    elif model == 'fsr_model.CNN_LSTM':
        trial.suggest_categorical('model_args/cnn_hidden_size', [8, 16, 32, 64, 128])
        trial.suggest_categorical('model_args/lstm_hidden_size', [8, 16, 32, 64, 128])
        trial.suggest_int('model_args/cnn_num_layer', 1, 8)
        trial.suggest_int('model_args/lstm_num_layer', 1, 8)
    elif model == 'fsr_model.ANN':
        trial.suggest_categorical('model_args/hidden_size', [8, 16, 32, 64, 128])
        trial.suggest_int('model_args/num_layer', 1, 8)
    trial.suggest_categorical('criterion', ['torch.nn.MSELoss'])
    trial.suggest_categorical('optimizer', [
        'torch.optim.Adam',
        'torch.optim.NAdam',
        'torch.optim.Adagrad',
        'torch.optim.RAdam',
        'torch.optim.SGD',
    ])
    trial.suggest_float('optimizer_args/lr', 1e-5, 1e-1, log=True)
    trial.suggest_categorical('scaler', [ 
        'sklearn.preprocessing.StandardScaler',
        'sklearn.preprocessing.MinMaxScaler',
        'sklearn.preprocessing.RobustScaler',
    ])
    return {
        'index_X': 'FSR_for_force',
        'index_y': 'force',
        'data_loader': 'fsr_data.get_index_splited_by_subject'
    }

In [2]:
import ray.tune
import ray.air
import ray.air.integrations.wandb
import ray.tune.schedulers
from fsr_trainable import FSR_Trainable
import ray.tune.search
import ray.tune.search.optuna

tuner = ray.tune.Tuner(
    trainable=ray.tune.with_resources(
        FSR_Trainable, {'cpu':2},
    ),
    tune_config=ray.tune.TuneConfig(
        num_samples=1000,
        scheduler=ray.tune.schedulers.ASHAScheduler(
            max_t=100,
            grace_period=1,
            reduction_factor=2,
            brackets=1,
            metric='rmse',
            mode='min',
        ),
        search_alg=ray.tune.search.optuna.OptunaSearch(
            space=define_searchspace,
            metric='rmse',
            mode='min',
        ),
    ), 
    run_config=ray.air.RunConfig(
        callbacks=[
            ray.air.integrations.wandb.WandbLoggerCallback(project='FSR-prediction'),
        ],
        checkpoint_config=ray.air.CheckpointConfig(
            num_to_keep=3,
            checkpoint_score_attribute='rmse',
            checkpoint_score_order='min',
            checkpoint_frequency=5,
            checkpoint_at_end=True,
        ),
    ), 
)

[I 2023-07-06 22:25:52,790] A new study created in memory with name: optuna


In [3]:
results = tuner.fit()

2023-07-05 22:11:00,321	INFO worker.py:1627 -- Started a local Ray instance. View the dashboard at 127.0.0.1:8265 
2023-07-05 22:11:02,058	INFO tune.py:226 -- Initializing Ray automatically. For cluster usage or custom Ray initialization, call `ray.init(...)` before `Tuner(...)`.


2023-07-05 22:11:02,110	INFO wandb.py:320 -- Already logged into W&B.


(_WandbLoggingActor pid=100917) wandb: Currently logged in as: seokjin. Use `wandb login --relogin` to force relogin
(_WandbLoggingActor pid=100917) wandb: Tracking run with wandb version 0.15.4
(_WandbLoggingActor pid=100917) wandb: Run data is saved locally in /home/seokj/ray_results/FSR_Trainable_2023-07-05_22-10-54/FSR_Trainable_ff527c6c_1_criterion=torch_nn_MSELoss,data_loader=fsr_data_get_index_splited_by_subject,index_X=FSR_for_force,index__2023-07-05_22-11-02/wandb/run-20230705_221114-ff527c6c
(_WandbLoggingActor pid=100917) wandb: Run `wandb offline` to turn off syncing.
(_WandbLoggingActor pid=100917) wandb: Syncing run FSR_Trainable_ff527c6c
(_WandbLoggingActor pid=100917) wandb: ⭐️ View project at https://wandb.ai/seokjin/FSR-prediction
(_WandbLoggingActor pid=100917) wandb: 🚀 View run at https://wandb.ai/seokjin/FSR-prediction/runs/ff527c6c
(_WandbLoggingActor pid=101089) wandb: Currently logged in as: seokjin. Use `wandb login --relogin` to force relogin
(_WandbLoggingAct

2023-07-06 02:09:12,114	WARNING util.py:315 -- The `callbacks.on_trial_result` operation took 0.777 s, which may be a performance bottleneck.
2023-07-06 02:09:12,118	WARNING util.py:315 -- The `process_trial_result` operation took 0.782 s, which may be a performance bottleneck.
2023-07-06 02:09:12,119	WARNING util.py:315 -- Processing trial results took 0.784 s, which may be a performance bottleneck. Please consider reporting results less frequently to Ray Tune.
2023-07-06 02:09:12,121	WARNING util.py:315 -- The `process_trial_result` operation took 0.785 s, which may be a performance bottleneck.


In [3]:
results = tuner.restore(
    path='/home/seokj/ray_results/FSR_Trainable_2023-07-05_22-10-54',
    trainable=FSR_Trainable
).fit()

Failed to read the results for 1 trials:
- /home/seokj/ray_results/FSR_Trainable_2023-07-05_22-10-54/FSR_Trainable_95f1fd86_911_criterion=torch_nn_MSELoss,data_loader=fsr_data_get_index_splited_by_subject,index_X=FSR_for_force,inde_2023-07-06_02-07-56
2023-07-06 22:26:04,398	INFO worker.py:1627 -- Started a local Ray instance. View the dashboard at 127.0.0.1:8265 
2023-07-06 22:26:07,234	INFO tune.py:226 -- Initializing Ray automatically. For cluster usage or custom Ray initialization, call `ray.init(...)` before `Tuner(...)`.


2023-07-06 22:26:07,404	INFO experiment_state.py:435 -- A local experiment checkpoint was found and will be used to restore the previous experiment state.
2023-07-06 22:26:07,492	WARNING trial_runner.py:418 -- Attempting to resume experiment from /home/seokj/ray_results/FSR_Trainable_2023-07-05_22-10-54. This will ignore any new changes to the specification.
2023-07-06 22:26:07,493	INFO trial_runner.py:422 -- Using the newest experiment state file found within the experiment directory: experiment_state-2023-07-06_19-49-18.json
2023-07-06 22:26:11,824	INFO wandb.py:320 -- Already logged into W&B.
(FSR_Trainable pid=1228) 2023-07-06 22:26:27,871	INFO trainable.py:918 -- Restored on 172.26.215.93 from checkpoint: /tmp/checkpoint_tmp_7a5e7a7f4f114d54bab81c7ff9f1ce70
(FSR_Trainable pid=1228) 2023-07-06 22:26:27,871	INFO trainable.py:927 -- Current state after restoring: {'_iteration': 65, '_timesteps_total': None, '_time_total': 51.325918436050415, '_episodes_total': None}


(_WandbLoggingActor pid=1446) wandb: Currently logged in as: seokjin. Use `wandb login --relogin` to force relogin
(FSR_Trainable pid=1231) 2023-07-06 22:26:28,098	INFO trainable.py:918 -- Restored on 172.26.215.93 from checkpoint: /tmp/checkpoint_tmp_2891af8d2a2445849f7d52b2c8ef6c93 [repeated 3x across cluster] (Ray deduplicates logs by default. Set RAY_DEDUP_LOGS=0 to disable log deduplication, or see https://docs.ray.io/en/master/ray-observability/ray-logging.html#log-deduplication for more options.)
(FSR_Trainable pid=1231) 2023-07-06 22:26:28,098	INFO trainable.py:927 -- Current state after restoring: {'_iteration': 70, '_timesteps_total': None, '_time_total': 54.64508366584778, '_episodes_total': None} [repeated 3x across cluster]
(_WandbLoggingActor pid=1446) wandb: wandb version 0.15.5 is available!  To upgrade, please run:
(_WandbLoggingActor pid=1446) wandb:  $ pip install wandb --upgrade
(_WandbLoggingActor pid=1446) wandb: Tracking run with wandb version 0.15.4
(_WandbLoggi